Create Customer Dimension Table

In [0]:
-- create the customer dimension table with added hash column and timestamp tracking
DROP TABLE IF EXISTS customer_dim CASCADE;
CREATE TABLE customer_dim ( 
customer_dim_id     bigint GENERATED BY DEFAULT AS IDENTITY(1, 1), 
c_customer_sk integer NOT NULL ENCODE az64 distkey,
c_first_name character(20) ENCODE lzo,
c_last_name character(30) ENCODE lzo,
c_current_addr_sk integer ENCODE az64,
c_birth_country character varying(20) ENCODE lzo,
c_email_address character(50) ENCODE lzo,
record_insert_ts    timestamp WITHOUT time ZONE DEFAULT current_timestamp ,
record_upd_ts       timestamp WITHOUT time ZONE DEFAULT NULL
)
SORTKEY (c_customer_sk);

Initial population of Customer Dimension Table

In [0]:
-- populate dimension and hash based off of (address and phone) as drivers
insert into customer_dim 
       (c_customer_sk, c_first_name,c_last_name, c_current_addr_sk, c_birth_country, c_email_address) 
select  c_customer_sk, c_first_name,c_last_name, c_current_addr_sk, c_birth_country, c_email_address
from "sample_data_dev"."tpcds"."customer";

Validate Customer Dimension Creation count and data

In [0]:
-- check customers count and look at sample data
select count(1) from customer_dim; 
select * from customer_dim limit 10;

Simulate customer table changes

In [0]:
-- create a source table with some updates and some inserts
-- Update- Email has changed for 100 customers 
drop table if exists src_customer;
create table src_customer distkey(c_customer_sk) as 
select c_customer_sk , c_first_name , c_last_name, c_current_addr_sk, c_birth_country, 'x'+c_email_address as c_email_address, getdate() as effective_dt
from   customer_dim 
where  c_email_address is not null
limit 100;


-- also let's add three completely new customers
insert into src_customer values 
(15000001, 'Customer#15','000001', 10001 ,'USA'    , 'Customer#15000001@gmail.com', getdate() ),
(15000002, 'Customer#15','000002', 10002 ,'MEXICO' , 'Customer#15000002@gmail.com', getdate() ),
(15000003, 'Customer#15','000003', 10003 ,'CANADA' , 'Customer#15000003@gmail.com', getdate() );

-- check source count
select count(1) from src_customer;

Before Merge command - Merge Source Table into Target Table

In [0]:
-- create another table for testing purposes
DROP TABLE if exists customer_dim2;
CREATE TABLE customer_dim2 AS SELECT * from customer_dim;

-- merge changes to dim customer
BEGIN TRANSACTION;

-- update current records
UPDATE customer_dim2
SET    c_first_name      = src.c_first_name      ,
       c_last_name       = src.c_last_name       , 
       c_current_addr_sk = src.c_current_addr_sk , 
       c_birth_country   = src.c_birth_country   , 
       c_email_address   = src.c_email_address   ,
       record_upd_ts     = current_timestamp
from   src_customer AS src
where  customer_dim2.c_customer_sk = src.c_customer_sk ;

-- Insert new records
INSERT INTO customer_dim2 (c_customer_sk, c_first_name,c_last_name, c_current_addr_sk, c_birth_country, c_email_address) 
select src.c_customer_sk, src.c_first_name,src.c_last_name, src.c_current_addr_sk, src.c_birth_country, src.c_email_address 
from   src_customer AS src
where  src.c_customer_sk NOT IN (select c_customer_sk from customer_dim2);

-- end merge operation
COMMIT TRANSACTION;

With Merge command - Merge Source Table into Target Table

In [0]:
MERGE INTO customer_dim using src_customer AS src ON customer_dim.c_customer_sk = src.c_customer_sk
WHEN MATCHED THEN UPDATE 
SET c_first_name      = src.c_first_name      ,
    c_last_name       = src.c_last_name       , 
    c_current_addr_sk = src.c_current_addr_sk , 
    c_birth_country   = src.c_birth_country   , 
    c_email_address   = src.c_email_address   ,
    record_upd_ts     = current_timestamp
WHEN NOT MATCHED THEN INSERT (c_customer_sk, c_first_name,c_last_name, c_current_addr_sk, c_birth_country, c_email_address) 
                      VALUES (src.c_customer_sk, src.c_first_name,src.c_last_name, src.c_current_addr_sk, src.c_birth_country, src.c_email_address );

Check Target Table changes

In [0]:
-- Check the changes
-- to get updates
select * 
from customer_dim
where record_upd_ts is not null;

-- to get the newly inserted rows we can make use window function as follows
select customer_dim_id,c_customer_sk ,c_first_name ,c_last_name ,c_current_addr_sk,c_birth_country ,c_email_address ,record_insert_ts ,record_upd_ts 
from 
( select rank() OVER (ORDER BY DATE_TRUNC('second',record_insert_ts) desc) AS rnk, 
         customer_dim_id,c_customer_sk ,c_first_name ,c_last_name ,c_current_addr_sk,c_birth_country ,c_email_address ,record_insert_ts ,record_upd_ts 
  from customer_dim
  where record_upd_ts is null)
where rnk = 1;


-- to do the same thing using Qualify clause
select * 
from customer_dim
where record_upd_ts is null
QUALIFY rank() OVER (ORDER BY DATE_TRUNC('second',record_insert_ts) desc) = 1 ;

-- To get all changes
select *
from (
select 'Updates' as operations, cd.* 
from   customer_dim as cd
where  cd.record_upd_ts is not null
union 
select 'Inserts' as operations, cd.* 
from customer_dim cd
where cd.record_upd_ts is null
QUALIFY rank() OVER (ORDER BY DATE_TRUNC('second',cd.record_insert_ts) desc) = 1 
) order by 1;